<a href="https://colab.research.google.com/github/FriendlyUser/bark_ai_text/blob/main/ai_voice_cloning_test.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
%pip install bark

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 18.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 49.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.6/135.6 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 76.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 67.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.7/10.7 MB 43.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.6/79.6 kB 7.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 4.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 17.2 MB/s eta 0:00:00
  Created wheel for encodec: filename=encodec-0.1.1-py3-none-any.whl size=45775 sha256=08f2dc648abd5c655d50e8f9a9044fbd2c1092a19c9eb913a8d964

In [21]:
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "0"


from IPython.display import Audio
import nltk  # we'll use this to split into sentences
import numpy as np
from scipy.io.wavfile import write as write_wav
from bark.generation import (
    generate_text_semantic,
    preload_models,
)
from bark.api import semantic_to_waveform
from bark import generate_audio, SAMPLE_RATE

In [4]:
preload_models()

Downloading: "https://dl.fbaipublicfiles.com/encodec/v0/encodec_24khz-d7cc33bc.th" to /root/.cache/torch/hub/checkpoints/encodec_24khz-d7cc33bc.th
100%|██████████| 88.9M/88.9M [00:00<00:00, 129MB/s]


In [6]:
script = """
Narrator: Jarret walks into the coffee shop and spots his friend Beta sitting at a table in the corner. He walks over and takes a seat across from him.

Jarret: Hey, Beta! How's it going?

Beta: Not bad, Jarret. How about you?

Jarret: Can't complain. I've been keeping an eye on the stock market lately.

Beta: Oh yeah? What have you been seeing?

Jarret: Well, have you heard about JP Morgan buying up banking stocks like FRC?

Beta: Yeah, I heard about that. It seems like they're trying to expand their reach in the banking industry.

Jarret: Exactly. It's a smart move for them. But I'm more interested in Tesla's stock. It seems to be tanking again.

Beta: Yeah, I saw that too. I think it's because of concerns about their production and delivery numbers.

Jarret: That could be it. But it's also possible that investors are just losing faith in the company's ability to turn a profit.

Beta: That's always a risk with high-growth companies like Tesla. But speaking of investing, have you read "The Intelligent Investor" by Benjamin Graham?

Jarret: No, I haven't. What's it about?

Beta: It's a classic book on value investing. Graham was Warren Buffett's mentor, so you can imagine how influential his ideas are.

Jarret: Interesting. I'll have to check it out.

Beta: Definitely do. It's a great way to learn about the principles of investing and how to analyze stocks.

Jarret: Thanks for the recommendation, Beta. I'll add it to my reading list.

Beta: No problem, Jarret. It's important to stay informed about the stock market if you want to be a successful investor.

Jarret: Absolutely. It's a complex and ever-changing system, but with the right knowledge, anyone can navigate it.

Beta: That's right. And with some luck, you might even make a profit!

Narrator: Jarret and Beta laugh as they finish their coffee and continue their conversation about the stock market.
"""

In [7]:
script = script.strip().split("\n")
script = [s.strip() for s in script if s]
script

['Narrator: Jarret walks into the coffee shop and spots his friend Beta sitting at a table in the corner. He walks over and takes a seat across from him.',
 "Jarret: Hey, Beta! How's it going?",
 'Beta: Not bad, Jarret. How about you?',
 "Jarret: Can't complain. I've been keeping an eye on the stock market lately.",
 'Beta: Oh yeah? What have you been seeing?',
 'Jarret: Well, have you heard about JP Morgan buying up banking stocks like FRC?',
 "Beta: Yeah, I heard about that. It seems like they're trying to expand their reach in the banking industry.",
 "Jarret: Exactly. It's a smart move for them. But I'm more interested in Tesla's stock. It seems to be tanking again.",
 "Beta: Yeah, I saw that too. I think it's because of concerns about their production and delivery numbers.",
 "Jarret: That could be it. But it's also possible that investors are just losing faith in the company's ability to turn a profit.",
 'Beta: That\'s always a risk with high-growth companies like Tesla. But spe

In [16]:
speaker_lookup = {"Jarret": "en_speaker_4", "Beta": "en_speaker_2", "Narrator": "en_speaker_9"}

In [17]:
pieces = []
silence = np.zeros(int(0.5*SAMPLE_RATE))
for line in script:
    speaker, text = line.split(": ")
    print(speaker, text)
    speaker_voice = speaker_lookup[speaker]
    print(speaker_voice)
    audio_array = generate_audio(text, history_prompt="en_speaker_6" )
    pieces += [audio_array, silence.copy()]

Narrator Jarret walks into the coffee shop and spots his friend Beta sitting at a table in the corner. He walks over and takes a seat across from him.
en_speaker_9


100%|██████████| 23/23 [00:21<00:00,  1.08it/s]


Jarret Hey, Beta! How's it going?
en_speaker_4


100%|██████████| 8/8 [00:07<00:00,  1.10it/s]


Beta Not bad, Jarret. How about you?
en_speaker_2


...

100%|██████████| 20/20 [00:18<00:00,  1.09it/s]


Beta That's right. And with some luck, you might even make a profit!
en_speaker_2


100%|██████████| 12/12 [00:11<00:00,  1.09it/s]


Narrator Jarret and Beta laugh as they finish their coffee and continue their conversation about the stock market.
en_speaker_9


100%|██████████| 14/14 [00:12<00:00,  1.09it/s]


In [18]:
Audio(np.concatenate(pieces), rate=SAMPLE_RATE)

In [23]:
write_wav("bark_generation.wav", SAMPLE_RATE, np.concatenate(pieces))